In [1]:
import requests
import json
import xlrd
import xlwt
from datetime import datetime,timedelta
import time
# 变量定义
login_url = "http://10.200.32.39/jingbo-api/api/server/login"
search_url = "http://10.200.32.39/jingbo-api/api/warehouse/dwDataItem/queryByItemNos"

login_push_url = "http://10.200.32.39/jingbo-api/api/server/login"
upload_url = "http://10.200.32.39/jingbo-api/api/dw/dataValue/pushDataValueList"

login_data = {
    "data": {
        "account": "api_dev",
        "password": "ZTEwYWRjMzk0OWJhNTlhYmJlNTZlMDU3ZjIwZjg4M2U=",
        "tenantHashCode": "8a4577dbd919675758d57999a1e891fe",
        "terminal": "API"
    },
    "funcModule": "API",
    "funcOperation": "获取token"
}

login_push_data = {
    "data": {
        "account": "api_dev",
        "password": "ZTEwYWRjMzk0OWJhNTlhYmJlNTZlMDU3ZjIwZjg4M2U=",
        "tenantHashCode": "8a4577dbd919675758d57999a1e891fe",
        "terminal": "API"
    },
    "funcModule": "API",
    "funcOperation": "获取token"
}

read_file_path_name = "液化气数据.xls"
one_cols = []
two_cols = []

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sn
import random
import time




from plotly import __version__
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

from sklearn import preprocessing

from pandas import Series,DataFrame

import matplotlib.pyplot as plt

import sklearn.datasets as datasets

#导入机器学习算法模型
from sklearn.linear_model import Lasso
from xgboost import XGBRegressor

import statsmodels.api as sm
try:
    from keras.preprocessing.sequence import TimeseriesGenerator
except:
    from tensorflow.keras.preprocessing.sequence import TimeseriesGenerator

import plotly.express as px
import plotly.graph_objects as go

import xgboost as xgb
from xgboost import plot_importance, plot_tree
from sklearn.metrics import mean_absolute_error
from statsmodels.tools.eval_measures import mse,rmse
from sklearn.model_selection import GridSearchCV
from xgboost import XGBRegressor
import warnings
import pickle

from sklearn.metrics import mean_squared_error

#切割训练数据和样本数据
from sklearn.model_selection import train_test_split

#用于模型评分
from sklearn.metrics import r2_score

le = preprocessing.LabelEncoder()

# print(__version__) # requires version >= 1.9.0


import cufflinks as cf
cf.go_offline()

random.seed(100)

%matplotlib inline

# 数据获取

def get_head_auth():
    login_res = requests.post(url=login_url, json=login_data, timeout=(3, 5))
    text = json.loads(login_res.text)
    if text["status"]:
        token = text["data"]["accessToken"]
        return token
    else:
        print("获取认证失败")
        return None


def get_data_value(token, dataItemNoList,date):
    search_data = {
        "data": {
            "date": date,
            "dataItemNoList": dataItemNoList
        },
        "funcModule": "数据项",
        "funcOperation": "查询"
    }
    headers = {"Authorization": token}
    search_res = requests.post(url=search_url, headers=headers, json=search_data, timeout=(3, 5))
    print(search_data)
    
    try:
        search_value = json.loads(search_res.text)["data"]
        print(search_value)
    except json.JSONDecodeError as e:
        print(f"Error decoding JSON: {e}")
        print("Response content:", search_res.text)
        return None 
    if search_value:
        return search_value
    else:
        print("今天没有新数据")
        return search_value



# xls文件处理





def write_xls(data):
    # 创建一个Workbook对象
    workbook = xlwt.Workbook()

    # 创建一个Sheet对象，可指定名称
    sheet = workbook.load('Sheet1')

    # 写入数据行
    for row_index, row_data in enumerate(data):
        for col_index, cell_data in enumerate(row_data):
            sheet.write(row_index, col_index, cell_data)

    # 保存Workbook到文件
    workbook.save(get_cur_time()[0] + '.xls')


def get_cur_time(date = ''):
    if date == '':
        now = datetime.now()
    else:
        now = date
    year = now.year
    month = now.month
    day = now.day

    if month < 10:
        month = "0" + str(month)
    if day < 10:
        day = "0" + str(day)
    cur_time = str(year) + str(month) + str(day)
    cur_time2 = str(year) + "-" + str(month) + "-" + str(day)
#     cur_time = '20231011'
#     cur_time2 = '2023-10-11'
    return cur_time, cur_time2



def get_head_push_auth():
    login_res = requests.post(url=login_push_url, json=login_push_data, timeout=(3, 5))
    text = json.loads(login_res.text)
    if text["status"]:
        token = text["data"]["accessToken"]
        return token
    else:
        print("获取认证失败")
        return None



def upload_data_to_system(token_push,date):
    data = {
        "funcModule": "数据表信息列表",
        "funcOperation": "新增",
        "data": [
            {"dataItemNo": "250855713|Forecast_Price|ACN",
             "dataDate": date,
             "dataStatus": "add",
             "dataValue": forecast_price()
             }

        ]
    }
    headers = {"Authorization": token_push}
    res = requests.post(url=upload_url, headers=headers, json=data, timeout=(3, 5))
    # print(res.text)

    
# def upload_data_to_system(token):
#     data = {
#         "funcModule": "数据表信息列表",
#         "funcOperation": "新增",
#         "data": [
#             {"dataItemNo": "C01100036|Forecast_ Price|ACN",
#              "dataDate": '20230706',
#              "dataStatus": "add",
#              "dataValue": 3780.0
#              }

#         ]
#     }
#     headers = {"Authorization": token}
#     res = requests.post(url=upload_url, headers=headers, json=data, timeout=(3, 5))
#     print(res.text)

price_list = []
    
def forecast_price():
    # df_test = pd.read_csv('定价模型数据收集0212.csv')
    df_test = pd.read_excel('液化气数据.xls')
    df_test.drop([0],inplace=True)
    try:
        df_test['Date']=pd.to_datetime(df_test['Date'],  format='%m/%d/%Y',infer_datetime_format=True)
    except:
        df_test['Date']=pd.to_datetime(df_test['Date'],  format=r'%Y-%m-%d',infer_datetime_format=True)


    df_test_1 = df_test
    df_test_1=df_test_1.fillna(df_test.ffill())
    df_test_1=df_test_1.fillna(df_test_1.bfill())

    # 选择用于模型训练的列名称
    col_for_training = df_test_1.columns




    import joblib
    Best_model_DalyLGPrice = joblib.load("日度价格预测_液化气最佳模型.pkl")
    # 最新的一天为最后一行的数据
   
    df_test_1_Day = df_test_1.tail(1)
    # 移除不需要的列
    df_test_1_Day.index = df_test_1_Day["Date"]
    df_test_1_Day = df_test_1_Day.drop(["Date"], axis= 1)
    df_test_1_Day=df_test_1_Day.drop('Price',axis=1)
    df_test_1_Day=df_test_1_Day.dropna()

    for col in df_test_1_Day.columns:
        df_test_1_Day[col] = pd.to_numeric(df_test_1_Day[col],errors='coerce')
    #预测今日价格，显示至小数点后两位
    Ypredict_Today=Best_model_DalyLGPrice.predict(df_test_1_Day)

    df_test_1_Day['日度预测价格']=Ypredict_Today
    print(df_test_1_Day['日度预测价格'])
    a = df_test_1_Day['日度预测价格']
    a = a[0]
    a = float(a)
    a = round(a,2)
    price_list.append(a)
    return a
def optimize_Model():
    from sklearn.model_selection import train_test_split
    from sklearn.impute  import SimpleImputer
    from sklearn.preprocessing import OrdinalEncoder
    from sklearn.feature_selection import SelectFromModel
    from sklearn.metrics import mean_squared_error, r2_score
    import pandas as pd

    pd.set_option('display.max_rows',40)  
    pd.set_option('display.max_columns',40)  
    df_test = pd.read_excel('液化气数据.xls')
    df_test.drop([0],inplace=True)
    try:
        df_test['Date']=pd.to_datetime(df_test['Date'],  format='%m/%d/%Y',infer_datetime_format=True)
    except:
        df_test['Date']=pd.to_datetime(df_test['Date'],  format=r'%Y-%m-%d',infer_datetime_format=True)

    
    #将缺失值补为前一个或者后一个数值
    df_test_1 = df_test
    df_test_1=df_test_1.fillna(df_test.ffill())
    df_test_1=df_test_1.fillna(df_test_1.bfill())
    df_test_1["Date"] = pd.to_datetime(df_test_1["Date"])
    df_test_1.index = df_test_1["Date"]
    df_test_1 = df_test_1.drop(["Date"], axis= 1)
    df_test_1 = df_test_1.astype('float')
    
    
    import numpy as np
    import pandas as pd
    from pandas import Series,DataFrame

    import matplotlib.pyplot as plt

    import sklearn.datasets as datasets

    #导入机器学习算法模型
    from sklearn.linear_model import Lasso
    from xgboost import XGBRegressor

    import statsmodels.api as sm
    try:
        from keras.preprocessing.sequence import TimeseriesGenerator
    except:
        from tensorflow.keras.preprocessing.sequence import TimeseriesGenerator

    import plotly.express as px
    import plotly.graph_objects as go

    import xgboost as xgb
    from xgboost import plot_importance, plot_tree
    from sklearn.metrics import mean_absolute_error
    from statsmodels.tools.eval_measures import mse,rmse
    from sklearn.model_selection import GridSearchCV
    from xgboost import XGBRegressor
    import warnings
    import pickle

    from sklearn.metrics import mean_squared_error

    #切割训练数据和样本数据
    from sklearn.model_selection import train_test_split

    #用于模型评分
    from sklearn.metrics import r2_score

    dataset1=df_test_1.drop('Price',axis=1)#.astype(float)

    y=df_test_1['Price']

    x=dataset1 

    train = x
    target = y

    #切割数据样本集合测试集
    X_train,x_test,y_train,y_true = train_test_split(train,target,test_size=0.2,random_state=0)

    #模型缩写
    Lasso =  Lasso(random_state=0)
    XGBR = XGBRegressor(random_state=0)
    #训练模型
    Lasso.fit(X_train,y_train)
    XGBR.fit(X_train,y_train)
    #模型拟合
    y_pre_Lasso = Lasso.predict(x_test)
    y_pre_XGBR = XGBR.predict(x_test)

    #计算Lasso、XGBR、RandomForestR、AdaBoostR、GradientBoostingR、BaggingRegressor各模型的R²
    Lasso_score = r2_score(y_true,y_pre_Lasso)
    XGBR_score=r2_score(y_true,y_pre_XGBR)

    #计算Lasso、XGBR的MSE和RMSE
    Lasso_MSE=mean_squared_error(y_true, y_pre_Lasso)
    XGBR_MSE=mean_squared_error(y_true, y_pre_XGBR)

    Lasso_RMSE=np.sqrt(Lasso_MSE)
    XGBR_RMSE=np.sqrt(XGBR_MSE)
    # 将不同模型的不同误差值整合成一个表格
    model_results = pd.DataFrame([['Lasso', Lasso_RMSE, Lasso_score],
                                 ['XgBoost', XGBR_RMSE, XGBR_score]],
                   columns = ['模型(Model)','均方根误差(RMSE)', 'R^2 score'])
    #将模型名称(Model)列设置为索引
    model_results1=model_results.set_index('模型(Model)')

    model_results1
    #定义plot_feature_importance函数，该函数用于计算特征重要性。此部分代码无需调整
    def plot_feature_importance(importance,names,model_type):
        feature_importance = np.array(importance)
        feature_names = np.array(names)

        data={'feature_names':feature_names,'feature_importance':feature_importance}
        fi_df = pd.DataFrame(data)

        fi_df.sort_values(by=['feature_importance'], ascending=False,inplace=True)

        plt.figure(figsize=(10,8))
        sn.barplot(x=fi_df['feature_importance'], y=fi_df['feature_names'])

        plt.title(model_type + " "+'FEATURE IMPORTANCE')
        plt.xlabel('FEATURE IMPORTANCE')
        plt.ylabel('FEATURE NAMES')
        from pylab import mpl
    %pylab
    mpl.rcParams['font.sans-serif'] = ['SimHei']
    ## Xgboost 模型参数优化-初步
    #参考: https://juejin.im/post/6844903661013827598 
    #每次调参时，备选参数数值以同数量级的1、3、10设置即可（比如设置1、3、10，或0.1、0.3、1.0，或0.01,0.03,0.10即可）

    from xgboost import XGBRegressor
    from sklearn.model_selection import GridSearchCV

    estimator = XGBRegressor(random_state=0,
        nthread=4,
        seed=0
    )
    parameters = {
        'max_depth': range (2, 11, 2),     # 树的最大深度
        'n_estimators': range (50, 101, 10),  # 迭代次数
        'learning_rate': [0.01, 0.03, 0.1, 0.3, 0.5, 1]
    }

    grid_search_XGB = GridSearchCV(
        estimator=estimator,
        param_grid=parameters,
    #     n_jobs = 10,
        cv = 3,
        verbose=True
    )

    grid_search_XGB.fit(X_train, y_train)
    #如果电脑在此步骤报错，可能是因为计算量太大，超过硬件可支持程度，可注释掉“n_jobs=10”一行

    best_parameters = grid_search_XGB.best_estimator_.get_params()
    y_pred = grid_search_XGB.predict(x_test)

    op_XGBR_score = r2_score(y_true,y_pred)
    op_XGBR_MSE= mean_squared_error(y_true, y_pred)
    op_XGBR_RMSE= np.sqrt(op_XGBR_MSE)

    model_results2 = pd.DataFrame([['Optimized_Xgboost', op_XGBR_RMSE, op_XGBR_score]],
                   columns = ['模型(Model)', '均方根误差(RMSE)', 'R^2 score'])
    model_results2=model_results2.set_index('模型(Model)')

    try:
        results = model_results1.append(model_results2, ignore_index = False)
    except:
        results = pd.concat([model_results1,model_results2],ignore_index=True)
    import pickle

    Pkl_Filename = "日度价格预测_液化气最佳模型.pkl"  

    with open(Pkl_Filename, 'wb') as file:  
       pickle.dump(grid_search_XGB, file)


   

def read_xls_data():
    global one_cols, two_cols
    # 打开 XLS 文件
    workbook = xlrd.open_workbook(read_file_path_name)

    # 获取所有表格名称
    # sheet_names = workbook.sheet_names()

    # 选择第一个表格
    sheet = workbook.sheet_by_index(0)

    # 获取行数和列数
    num_rows = sheet.nrows
    # num_cols = sheet.ncols

    # 遍历每一行，获取单元格数据
    # for i in range(num_rows):
    #     row_data = sheet.row_values(i)
    #     one_cols.append(row_data)
    #     two_cols.append(row_data[1])

    row_data = sheet.row_values(1)
    one_cols = row_data

    # 关闭 XLS 文件
    # workbook.close()



def start(date=''):
    read_xls_data()

    token = get_head_auth()
    if not token:
        return
    token_push = get_head_push_auth()
    if not token_push:
        return
    cur_time,cur_time2 = getNow(date)
    datas = get_data_value(token, one_cols[1:],cur_time)
#     if not datas:
#         return

    # data_list = [two_cols, one_cols]
    append_rows = [cur_time2]
    dataItemNo_dataValue = {}
    for data_value in datas:
        if "dataValue" not in data_value:
            print(data_value)
            dataItemNo_dataValue[data_value["dataItemNo"]] = ""
        else:
            dataItemNo_dataValue[data_value["dataItemNo"]] = data_value["dataValue"]
      
    for value in one_cols[1:]:
        if value in dataItemNo_dataValue:
            append_rows.append(dataItemNo_dataValue[value])
        else:
            append_rows.append("")
    save_xls(append_rows)
    optimize_Model()
    upload_data_to_system(token_push,cur_time)
    
    
    
    # data_list.append(three_cols)
    # write_xls(data_list)

def getNow(date='',offset=0):
    if date == '':
        from datetime import datetime
        now = datetime.now() - timedelta(days=offset)
    else:
        try:
            date = datetime.strptime(date, "%Y-%m-%d")
        except:
            date = datetime.strptime(date, "%Y%m%d")
        now = date

    year = now.year
    month = now.month
    day = now.day

    if month < 10:
        month = "0" + str(month)
    if day < 10:
        day = "0" + str(day)
    cur_time = str(year) + str(month) + str(day)
    cur_time2 = str(year) + "-" + str(month) + "-" + str(day)
    return cur_time,cur_time2
    
def start_1(date=''):
    read_xls_data()

    token = get_head_auth()
    if not token:
        return
    
    cur_time,cur_time2 = getNow(date)
    datas = get_data_value(token, one_cols[1:],date=cur_time)
#     if not datas:
#         return

    # data_list = [two_cols, one_cols]
    append_rows = [cur_time2]
    dataItemNo_dataValue = {}
    for data_value in datas:
        if "dataValue" not in data_value:
            print(data_value)
            dataItemNo_dataValue[data_value["dataItemNo"]] = ""
        else:
            dataItemNo_dataValue[data_value["dataItemNo"]] = data_value["dataValue"]
       
    for value in one_cols[1:]:
        if value in dataItemNo_dataValue:
            append_rows.append(dataItemNo_dataValue[value])
        else:
            append_rows.append("")
    save_xls_1(append_rows)

    
    # data_list.append(three_cols)
    # write_xls(data_list)
    
def save_xls_1(append_rows):

    # 打开xls文件
    workbook = xlrd.open_workbook('液化气数据.xls')

    # 获取所有sheet的个数
    sheet_count = len(workbook.sheet_names())

    # 获取所有sheet的名称
    sheet_names = workbook.sheet_names()

    new_workbook = xlwt.Workbook()
    for i in range(sheet_count):
        # 获取当前sheet
        sheet = workbook.sheet_by_index(i)

        # 获取sheet的行数和列数
        row_count = sheet.nrows - 1
        col_count = sheet.ncols
        # 获取原有数据
        data = []
        for row in range(row_count):
            row_data = []
            for col in range(col_count):
                row_data.append(sheet.cell_value(row, col))
            data.append(row_data)
        # 创建xlwt的Workbook对象
        # 创建sheet
        new_sheet = new_workbook.add_sheet(sheet_names[i])

        # 将原有的数据写入新的sheet
        for row in range(row_count):
            for col in range(col_count):
                new_sheet.write(row, col, data[row][col])

        if i == 0:
            # 在新的sheet中添加数据
            for col in range(col_count):
                new_sheet.write(row_count, col, append_rows[col])

    # 保存新的xls文件
    new_workbook.save("液化气数据.xls")    

    
    
    
def check_data(dataItemNo):
    token = get_head_auth()
    if not token:
        return

    datas = get_data_value(token, dataItemNo)
    if not datas:
        return


def save_xls(append_rows):

    # 打开xls文件
    workbook = xlrd.open_workbook('液化气数据.xls')

    # 获取所有sheet的个数
    sheet_count = len(workbook.sheet_names())

    # 获取所有sheet的名称
    sheet_names = workbook.sheet_names()

    new_workbook = xlwt.Workbook()
    for i in range(sheet_count):
        # 获取当前sheet
        sheet = workbook.sheet_by_index(i)

        # 获取sheet的行数和列数
        row_count = sheet.nrows
        col_count = sheet.ncols
        # 获取原有数据
        data = []
        for row in range(row_count):
            row_data = []
            for col in range(col_count):
                row_data.append(sheet.cell_value(row, col))
            data.append(row_data)
        # 创建xlwt的Workbook对象
        # 创建sheet
        new_sheet = new_workbook.add_sheet(sheet_names[i])

        # 将原有的数据写入新的sheet
        for row in range(row_count):
            for col in range(col_count):
                new_sheet.write(row, col, data[row][col])

        if i == 0:
            # 在新的sheet中添加数据
            for col in range(col_count):
                new_sheet.write(row_count, col, append_rows[col])

    # 保存新的xls文件
    new_workbook.save("液化气数据.xls")



C:\Users\Administrator\Anaconda3\lib\site-packages\statsmodels\compat\pandas.py:49: FutureWarning:

The Panel class is removed from pandas. Accessing it from the top-level namespace will also be removed in the next version



In [ ]:

if __name__ == "__main__":
    print('运行中')
    # 需要单独运行放开
#     start()
#     start_1(date='2025-01-22')
#     start_1()

    # 每天定时12点运行
    while True:
        try:
            # 获取当前时间
            current_time = time.strftime("%H:%M:%S", time.localtime())
            current_time_1 = time.strftime("%H:%M:%S", time.localtime())
#             print(current_time_1)

            # 判断当前时间是否为执行任务的时间点
            if current_time == "09:15:00":
                print("执行定时任务")
                start()

                # 休眠1秒钟，避免过多占用CPU资源
                time.sleep(1)

            elif current_time_1 == "20:00:00":
                print("更新数据")
                start_1()
                time.sleep(1)
        except:
            print('执行错误')
        time.sleep(1)


    # 检测数据准确性, 需要检测放开
    # check_data("100028098|LISTING_PRICE")
    # check_data("9137070016544622XB|DAY_Yield")


运行中
13:38:57
13:38:58
13:38:59
13:39:00
13:39:01
13:39:02
13:39:03
13:39:04
13:39:05
13:39:06
13:39:07
13:39:08
13:39:09
13:39:10
13:39:11
13:39:12
13:39:13
13:39:14
13:39:15
13:39:16
13:39:17
13:39:18
13:39:19
13:39:20
13:39:21
13:39:22
13:39:23
13:39:24
13:39:25
13:39:26
13:39:27
13:39:28
13:39:29
13:39:30
13:39:31
13:39:32
13:39:33
13:39:34
13:39:35
13:39:36
13:39:37
13:39:38
13:39:39
13:39:40
13:39:41
13:39:42
13:39:43
13:39:44
13:39:45
13:39:46
13:39:47
13:39:48
13:39:49
13:39:50
13:39:51
13:39:52
13:39:53
13:39:54
13:39:55
13:39:56
13:39:57
13:39:58
13:39:59
13:40:00
执行定时任务
{'data': {'date': '20250123', 'dataItemNoList': ['251926669|STRIKE_PRICE', 'C01100008|CORTED_VALUE', 'C01100008|AUCTION_MAX_PRICE', 'C01100008|YEDAY_AMOUNT', 'ICE_CL0_LAST_YEDAY_PRICE\n', '100028046|LISTING_PRICE', 'C01100008|PLAN_SALE', '91370200163576944B|C01100008|STRIKE_PRICE', '9137078672073757X8|C01100008|STRIKE_PRICE', '91370500674526498A|C01100008|STRIKE_PRICE', '91370305773165341A|C01100008|STRIKE_PRI

C:\Users\Administrator\Anaconda3\lib\site-packages\IPython\core\magics\pylab.py:160: UserWarning:

pylab import has clobbered these variables: ['datetime', 'random', 'plot', '__version__']
`%matplotlib` prevents importing * from pylab and numpy



Date
2025-01-23    5399.734863
Name: 日度预测价格, dtype: float32
13:40:46
13:40:47
13:40:48
13:40:49
13:40:50
13:40:51
13:40:52
13:40:53
13:40:54
13:40:55
13:40:56
13:40:57
13:40:58
13:40:59
13:41:00
13:41:01
13:41:02
13:41:03
13:41:04
13:41:05
13:41:06
13:41:07
13:41:08
13:41:09
13:41:10
13:41:11
13:41:12
13:41:13
13:41:14
13:41:15
13:41:16
13:41:17
13:41:18
13:41:19
13:41:20
13:41:21
13:41:22
13:41:23
13:41:24
13:41:25
13:41:26
13:41:27
13:41:28
13:41:29
13:41:30
13:41:31
13:41:32
13:41:33
13:41:34
13:41:35
13:41:36
13:41:37
13:41:38
13:41:39
13:41:40
13:41:41
13:41:42
13:41:43
13:41:44
13:41:45
13:41:46
13:41:47
13:41:48
13:41:49
13:41:50
13:41:51
13:41:52
13:41:53
13:41:54
13:41:55
13:41:56
13:41:57
13:41:58
13:41:59
13:42:00
13:42:01
13:42:02
13:42:03
13:42:04
13:42:05
13:42:06
13:42:07
13:42:08
13:42:09
13:42:10
13:42:11
13:42:12
13:42:13
13:42:14
13:42:15
13:42:16
13:42:17
13:42:18
13:42:19
13:42:20
13:42:21
13:42:22
13:42:23
13:42:24
13:42:25
13:42:26
13:42:27
13:42:28
13:42:29
13:4

In [ ]:
# from datetime import datetime, timedelta

# start_date = datetime(2025, 1, 21)
# end_date = datetime(2025, 1, 23)

# while start_date < end_date:
#     print(start_date.strftime('%Y%m%d'))
#     start(start_date)
#     # time.sleep(1)
#     # start_2(start_date)
#     start_date += timedelta(days=1)
#     time.sleep(5)

# print(price_list)